In [1]:
import requests
import re
import urllib.parse
import time
import json

/Users/borangoksel/Documents/GitHub/assembly-zone-scraping/venv/lib/python3.9/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


In [2]:
def send_request(session, url, data, headers, lat, lng):
    # Update latitude and longitude in the data dictionary
    data["lat"] = str(lat)
    data["lng"] = str(lng)
    
    # Measure request time
    start_time = time.time()
    
    response = session.post(url, data=data, headers=headers)
    elapsed_time = time.time() - start_time  # Calculate elapsed time
    
    # Print the response time
    print(f"Response received in {elapsed_time:.2f} seconds for lat: {lat}, lng: {lng}")  
    
    # Check for a successful response and return the result
    if response.status_code == 200:
        return response.json()
    else:
        print(f"Error: {response.status_code}, {response.text}")
        return None


In [3]:
# Function to parse the curl bash command into usable components
def clean_curl_request(curl_command):
    # Extract the URL
    url_pattern = r"curl '(.*?)'"
    match = re.search(url_pattern, curl_command)
    if match:
        url = match.group(1)
    else:
        raise ValueError("URL not found in the curl command")

    # Extract headers
    headers = {}
    header_pattern = r"-H '([^:]+): (.*?)'"
    for header_match in re.finditer(header_pattern, curl_command):
        header_name = header_match.group(1)
        header_value = header_match.group(2)
        headers[header_name] = header_value

    # Extract data
    data_pattern = r"--data-raw '(.*?)'"
    match = re.search(data_pattern, curl_command)
    data = {}
    if match:
        data_string = match.group(1)
        data_items = data_string.split("&")
        for item in data_items:
            key, value = item.split("=")
            data[key] = urllib.parse.unquote(value)

    # Parse URL for host and path
    parsed_url = urllib.parse.urlparse(url)
    host = parsed_url.netloc
    path = parsed_url.path + ("?" + parsed_url.query if parsed_url.query else "")

    return host, path, data, headers

In [48]:
host, path, data, headers = clean_curl_request("""
curl 'https://www.turkiye.gov.tr/afet-ve-acil-durum-yonetimi-acil-toplanma-alani-sorgulama?harita=goster&submit' \
  -H 'Accept: application/json, text/javascript, */*; q=0.01' \
  -H 'Accept-Language: en-US,en;q=0.9' \
  -H 'Connection: keep-alive' \
  -H 'Content-Type: application/x-www-form-urlencoded; charset=UTF-8' \
  -H 'Cookie: w3p=3352537280.20480.0000; _uid=1732219586-384a1de9-4e26-4ca2-ab3d-ea0c7ce3dd86; ridbb=WyI1ZWZjYWJjN2E5YzNiY2M4ZDY4OWExMGIwN2IwMTcyMmNjZDc5NjUzYyJd; language=tr_TR.UTF-8; TURKIYESESSIONID=otcqd1hsu3nn4gfgtd321n6gjn; TS015d3f68=015c1cbb6d3207e3e26d2a718d4d33aaac6699669de6ad8b89d410c74708742e7ff2e2f90b3810e79e0ca4d2a65afb630eee75863c; _lastptts=1736943397' \
  -H 'Origin: https://www.turkiye.gov.tr' \
  -H 'Referer: https://www.turkiye.gov.tr/afet-ve-acil-durum-yonetimi-acil-toplanma-alani-sorgulama?harita=goster' \
  -H 'Sec-Fetch-Dest: empty' \
  -H 'Sec-Fetch-Mode: cors' \
  -H 'Sec-Fetch-Site: same-origin' \
  -H 'User-Agent: Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/130.0.0.0 Safari/537.36 OPR/115.0.0.0' \
  -H 'X-Requested-With: XMLHttpRequest' \
  -H 'sec-ch-ua: "Chromium";v="130", "Opera";v="115", "Not?A_Brand";v="99"' \
  -H 'sec-ch-ua-mobile: ?0' \
  -H 'sec-ch-ua-platform: "macOS"' \
  --data-raw 'pn=%2Fafet-ve-acil-durum-yonetimi-acil-toplanma-alani-sorgulama&ajax=1&token=%7B3CAD3B-B80C08-767A90-A2C766-E24EFF-8429AE-7B4DF7-478388%7D&islem=getAlanlarForNokta&lat=39.791366817301665&lng=32.82671752174776'
""")

In [51]:
url = f"https://{host}{path}"
session = requests.Session()
session.headers.update(headers)

print(send_request(session, url, data, headers, '41.11500146762486','29.899223470383866'))

Response received in 0.12 seconds for lat: 41.11500146762486, lng: 29.899223470383866
{'features': [{'geometry': {'coordinates': [[[29.905289729, 41.108041951], [29.905343545, 41.107856166], [29.905306157, 41.107570242], [29.905275147, 41.107229528], [29.905193364, 41.10715084], [29.90513354, 41.107134115], [29.904748495, 41.107662698], [29.904469687, 41.108009723], [29.904999754, 41.107988329], [29.905210005, 41.108025854], [29.905289729, 41.108041951]], [[29.905026805, 41.107916225], [29.904976143, 41.107879498], [29.90496079, 41.107885928], [29.904934046, 41.107865656], [29.904990814, 41.107816863], [29.905026536, 41.107839049], [29.905067214, 41.107806398], [29.905117877, 41.10784224], [29.905026805, 41.107916225]]], 'type': 'Polygon'}, 'type': 'Feature', 'properties': {'tesis_adi': 'Kadıköy Tapulama Harici Alan', 'il_adi': 'İSTANBUL', 'sokak_adi': 'EBABİL', 'ilce_adi': 'ŞİLE', 'mahalle_adi': 'KADIKÖY', 'x': 29.90502259184322, 'y': 41.10767745664887, 'tabela_kod': 'YOK', 'id': 1513

In [ ]:
from shapely.geometry import Polygon

coordinates = send_request(session, url, data, headers, '41.11500146762486','29.899223470383866')['features'][1].get('geometry').get('coordinates')[0]

# Create Shapely Polygon
polygon = Polygon(coordinates).wkt

# Get WKT format
#wkt_polygon = polygon.wkt
#print(wkt_polygon)

Response received in 0.04 seconds for lat: 41.11500146762486, lng: 29.899223470383866


AttributeError: 'str' object has no attribute 'wkt'

In [53]:
from shapely.geometry import Polygon

coordinates = send_request(session, url, data, headers, '41.11500146762486','29.899223470383866')['features'][1].get('geometry').get('coordinates')[0]

# Create Shapely Polygon
polygon = Polygon(coordinates).wkt

print(send_request(session, url, data, headers, '41.11500146762486','29.899223470383866'))
# Get WKT format
print(polygon)

Response received in 0.07 seconds for lat: 41.11500146762486, lng: 29.899223470383866
Response received in 0.07 seconds for lat: 41.11500146762486, lng: 29.899223470383866
{'features': [{'geometry': {'coordinates': [[[29.905289729, 41.108041951], [29.905343545, 41.107856166], [29.905306157, 41.107570242], [29.905275147, 41.107229528], [29.905193364, 41.10715084], [29.90513354, 41.107134115], [29.904748495, 41.107662698], [29.904469687, 41.108009723], [29.904999754, 41.107988329], [29.905210005, 41.108025854], [29.905289729, 41.108041951]], [[29.905026805, 41.107916225], [29.904976143, 41.107879498], [29.90496079, 41.107885928], [29.904934046, 41.107865656], [29.904990814, 41.107816863], [29.905026536, 41.107839049], [29.905067214, 41.107806398], [29.905117877, 41.10784224], [29.905026805, 41.107916225]]], 'type': 'Polygon'}, 'type': 'Feature', 'properties': {'tesis_adi': 'Kadıköy Tapulama Harici Alan', 'il_adi': 'İSTANBUL', 'sokak_adi': 'EBABİL', 'ilce_adi': 'ŞİLE', 'mahalle_adi': 'KAD

In [15]:
def load_geojson(filepath, ilce):
    """
    Opens up the source file and extracts the features for given district
    features: properties,id,name,geometry,geometry_type
    """
    with open(filepath, 'r', encoding='utf-8') as file:
        data = json.load(file)
    return [feature for feature in data["features"] if feature["properties"].get("name") == ilce] 

In [16]:
a = load_geojson('./istanbul-admin-level-8-without-centers.geojson','Kadıköy Mahallesi')

In [ ]:
print(a[0].get('properties'))


{'@id': 'relation/1275322', 'admin_level': '8', 'boundary': 'administrative', 'name': 'Kadıköy Mahallesi', 'network': 'TR34-villages', 'type': 'boundary'}


In [ ]:
with open('./istanbul-admin-level-8-without-centers.geojson', 'r', encoding='utf-8') as file:
        data = json.load(file)
a = [feature for feature in data["features"] if feature["properties"].get("name") == 'Kadıköy Mahallesi']

In [3]:
data['features'][0].get('properties').get('@id')

'relation/1275322'

In [9]:
import json

with open('./istanbul-admin-level-8-without-centers.geojson', 'r', encoding='utf-8') as file:
    data = json.load(file)

data

{'type': 'FeatureCollection',
 'generator': 'overpass-ide',
 'copyright': 'The data included in this document is from www.openstreetmap.org. The data is made available under ODbL.',
 'timestamp': '2020-05-29T19:00:02Z',
 'features': [{'type': 'Feature',
   'properties': {'@id': 'relation/1275322',
    'admin_level': '8',
    'boundary': 'administrative',
    'name': 'Kadıköy Mahallesi',
    'network': 'TR34-villages',
    'type': 'boundary'},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[29.8958993, 41.1042008],
      [29.8973613, 41.1045774],
      [29.8980985, 41.1046245],
      [29.902022, 41.1060085],
      [29.9024469, 41.1046151],
      [29.9041962, 41.1053024],
      [29.9046835, 41.104794],
      [29.9064079, 41.1040031],
      [29.9075075, 41.103231],
      [29.9094942, 41.1024966],
      [29.9104688, 41.1016492],
      [29.9109686, 41.1023177],
      [29.9118308, 41.1017904],
      [29.9123681, 41.1015268],
      [29.912768, 41.1016868],
      [29.912718, 41.103014

In [10]:
n_names = []
for i in data['features']:
    n_names.append(i.get('properties').get('name'))


In [11]:
len(n_names)

972

In [12]:
a = ['aa']

len(a)
len()








TypeError: len() takes exactly one argument (0 given)

In [14]:
import os
completed_neighborhoods = []

directory = os.fsencode('./results')
for file in os.listdir(directory):
    filename = os.fsdecode(file)
    if filename.endswith(".csv"): 
        completed_neighborhoods.append((os.path.splitext(os.path.basename(filename))[0]).split('.',1)[0])
        continue
    else:
        continue

In [15]:
len(completed_neighborhoods)

972